# EDA EMart

In [1]:
# Importing libraries, reading the data & cheking the shape of it.
import re
import os
import datetime
import warnings
import pandas as pd
import numpy as np
import datetime as dt
from collections import Counter
import matplotlib.pyplot as plt
%matplotlib inline
import seaborn as sns
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots


# Probablity Distribution / Hypothesis Testing
from scipy import stats
from scipy.stats import binom, norm, poisson, expon, geom, lognorm, levene, kstest, shapiro
from scipy.stats import ttest_1samp, ttest_ind, ttest_rel # T-test
from scipy.stats import chi2, chisquare, chi2_contingency # Chi-square test
from scipy.stats import pearsonr, spearmanr               # Corelation test
from scipy.stats import f_oneway                          # ANOVA
from statsmodels.stats.multicomp import MultiComparison

# Pre-processing Libraries
#!pip install category_encoders
#from category_encoders import TargetEncoder
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import OneHotEncoder, LabelEncoder, StandardScaler, MinMaxScaler
from sklearn.model_selection import train_test_split, KFold, cross_val_score, cross_validate, GridSearchCV, RandomizedSearchCV, learning_curve
from sklearn.metrics import (
    ConfusionMatrixDisplay, RocCurveDisplay, PrecisionRecallDisplay,
    accuracy_score, confusion_matrix, classification_report,
    roc_auc_score, roc_curve, auc, precision_recall_curve,
    mean_squared_error, mean_absolute_error,
    mean_absolute_percentage_error, r2_score, silhouette_score )
#from statsmodels.stats.outliers_influence import variance_inflation_factor

# Dimension Reduction Libraries
from imblearn.over_sampling import SMOTE
from sklearn.decomposition import PCA
from sklearn.manifold import TSNE
from sklearn.feature_selection import SelectKBest, chi2, f_classif, mutual_info_classif, SelectFromModel

# Transformation Libraries
from sklearn.compose import ColumnTransformer

# PipeLine Liraries
from sklearn.pipeline import Pipeline

# Machine Learning Libraries -- Classification / Regression Libraries
from xgboost import XGBClassifier
from sklearn.linear_model import LinearRegression, LogisticRegression, SGDClassifier
from sklearn.ensemble import RandomForestClassifier, BaggingClassifier, GradientBoostingClassifier, AdaBoostClassifier, AdaBoostRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.naive_bayes import GaussianNB
from sklearn.svm import SVC
#from catboost import CatBoostClassifier
from lightgbm import LGBMClassifier
from xgboost import XGBClassifier


#Clustering Libraries
import scipy.cluster.hierarchy as shc
from sklearn.impute import KNNImputer
from sklearn.cluster import MiniBatchKMeans, KMeans, AgglomerativeClustering
from sklearn.mixture import GaussianMixture

# Time Series Libraries
#!pip install fbprophet
import statsmodels.api as sm
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf
from statsmodels.tsa.statespace.sarimax import SARIMAX

warnings.filterwarnings("ignore")
datapath = os.getcwd() + "\\data\\"

dfProducts = pd.read_fwf(datapath + 'Products.csv', encoding='ISO-8859-1',header=None)
dfProducts = dfProducts[0].str.split(',', expand=True)
dfProducts.drop(columns=[10, 11, 12], inplace=True)
dfProducts.columns = dfProducts.iloc[0]
dfProducts = dfProducts[1:]
dfProducts.rename(columns={"Product Name": "ProductName", "Unit Cost USD": "UnitCostUSD", "Unit Price USD": "UnitPriceUSD"}, inplace=True)

# Null values of products
dfProducts.dropna(how='all', inplace=True)
dfProducts['Category'].fillna('Unknown', inplace=True)
dfProducts['Subcategory'].fillna('Unknown', inplace=True)

dfProducts.drop_duplicates(keep="first", inplace=True)
dfProducts['UnitPriceUSD'] = dfProducts['UnitPriceUSD'].str.extract(r'(\d+.\d+)').astype('float64')
dfProducts['UnitCostUSD'] = dfProducts['UnitCostUSD'].str.extract(r'(\d+.\d+)').astype('float64')

dfCustomers = pd.read_fwf(datapath + 'Customers.csv', encoding='ISO-8859-1',header=None)
dfCustomers = dfCustomers[0].str.split(',', expand=True)
dfCustomers.columns = dfCustomers.iloc[0]
dfCustomers = dfCustomers[1:]
dfCustomers.dropna(how='all', inplace=True)
dfCustomers.drop_duplicates(keep="first", inplace=True)

dfSales = pd.read_fwf(datapath + 'Sales.csv', encoding='ISO-8859-1',header=None)
dfSales = dfSales[0].str.split(',', expand=True)
dfSales.columns = dfSales.iloc[0]
dfSales = dfSales[1:]
dfSales.rename(columns={"Order Number": "OrderNumber", "Line Item": "LineItem", "Order Date": "OrderDate", "Delivery Date": "DeliveryDate"}, inplace=True)
dfSales.dropna(how='all', inplace=True)
dfSales.drop_duplicates(keep="first", inplace=True)

print("Products Shape:", dfProducts.shape)
print("Customers Shape:", dfCustomers.shape)
print("Sales Shape:", dfSales.shape)

Products Shape: (2517, 10)
Customers Shape: (15266, 10)
Sales Shape: (62884, 9)


# Products Overview

In [5]:
def preProcess_Prod(products):
  products['Category'].replace(['Audio', 'Aud', 'Au', 'Audi'], 'Audio', inplace=True)
  products['Category'].replace(['Computers', 'C', 'Compute', 'Compu', 'Comput'], 'Computers', inplace=True)
  products['Category'].replace(['Cameras and camcorders', 'Cameras and camc', 'Cameras and camcor', 'Cameras and ca', 'Cameras and c', 'Cameras and cam', 'Cameras and camcorde', 'Cameras and camcorder', 'Cameras an', 'Cameras and', 'Cameras', 'Cameras', 'Cameras a', 'Cameras and camco', 'Cameras and camcord'], 'Cam & Recorder', inplace=True)
  products['Category'].replace(['Cell phone', 'Ce', 'Cell phon', 'Cell p', 'Cell pho', 'Cell', 'Cel', 'Cell ph', 'Cell phones'], 'CellPhone', inplace=True)
  products['Category'].replace(['02', '03', '04', '07', '08', ''], 'Unknown', inplace=True)
  products['CategoryKey'].replace(['01', '02', '03', '04', '05', '06', '07', '08', '0', '0802'], 'Unknown', inplace=True)
  products['CategoryKey'].replace([' Sca', ' Scann'], 'Scanners', inplace=True)
  products['CategoryKey'].replace([' Scanners & Fax"'], 'Scanners & Fax', inplace=True)

  products['Subcategory'].replace(['"Printers'], 'Printers', inplace=True)
  products['Subcategory'].replace(['0201', '0203', '0301', '0305', '08', '$159.00 ', '$158.00 ', '0405', '0702', '0801', '199.99 "', '0804', '0805'], 'Unknown', inplace=True)
  products['Subcategory'].replace(['Cameras & Camcorders Accessories'], 'CamCord Accessories', inplace=True)

preProcess_Prod(dfProducts)
dfProducts.head()

0 ProductKey                          ProductName    Brand   Color  \
1          1  Contoso 512MB MP3 Player E51 Silver  Contoso  Silver   
2          2    Contoso 512MB MP3 Player E51 Blue  Contoso    Blue   
3          3     Contoso 1G MP3 Player E100 White  Contoso   White   
4          4    Contoso 2G MP3 Player E200 Silver  Contoso  Silver   
5          5       Contoso 2G MP3 Player E200 Red  Contoso     Red   

0  UnitCostUSD  UnitPriceUSD SubcategoryKey Subcategory CategoryKey Category  
1         6.62         12.99           0101     MP4&MP3     Unknown    Audio  
2         6.62         12.99           0101     MP4&MP3     Unknown    Audio  
3         7.40         14.52           0101     MP4&MP3     Unknown    Audio  
4        11.00         21.57           0101     MP4&MP3     Unknown    Audio  
5        11.00         21.57           0101     MP4&MP3     Unknown    Audio

# Customer Overview

In [6]:
def preProcess_Customers(products):
  dfCustomers.rename(columns={"Zip Code": "ZipCode", "State Code": "StateCode"}, inplace=True)

  dfCustomers["Country"].replace('German', 'Germany', inplace=True)
  dfCustomers["Country"].replace('', None, inplace=True)
  dfCustomers["Country"].replace(['Unite', 'U', 'United Kingd', 'United K', 'United King', 'United', 'United Ki', 'United Kingdo', 'Uni', 'Unit', 'United Kin', 'Un'], 'United Kingdom', inplace=True)

  dfCustomers["Continent"].replace('Austr', 'Australia', inplace=True)
  dfCustomers["Continent"].replace('', None, inplace=True)
  dfCustomers["Continent"].replace(['North Ameri', 'North Americ', 'North Amer'], 'North America', inplace=True)
  dfCustomers["Continent"].replace(['Europ', 'Eu', 'E', 'Euro', 'Eur'], 'Europe', inplace=True)

preProcess_Customers(dfProducts)
dfCustomers.head()

0 CustomerKey  Gender               Name            City StateCode  \
1         301  Female      Lilly Harding  WANDEARAH EAST        SA   
2         325  Female       Madison Hull      MOUNT BUDD        WA   
3         554  Female      Claire Ferres       WINJALLOK       VIC   
4         786    Male  Jai Poltpalingada    MIDDLE RIVER        SA   
5        1042    Male    Aidan Pankhurst   TAWONGA SOUTH       VIC   

0              State ZipCode    Country  Continent    Birthday  
1    South Australia    5523  Australia  Australia    7/3/1939  
2  Western Australia    6522  Australia  Australia   9/27/1979  
3           Victoria    3380  Australia  Australia   5/26/1947  
4    South Australia    5223  Australia  Australia   9/17/1957  
5           Victoria    3698  Australia  Australia  11/19/1965

# Sales OverView

In [7]:
dfSales.head()

0 OrderNumber LineItem OrderDate DeliveryDate CustomerKey StoreKey ProductKey  \
1      366000        1  1/1/2016                   265598       10       1304   
2      366001        1  1/1/2016    1/13/2016     1269051        0       1048   
3      366001        2  1/1/2016    1/13/2016     1269051        0       2007   
4      366002        1  1/1/2016    1/12/2016      266019        0       1106   
5      366002        2  1/1/2016    1/12/2016      266019        0        373   

0 Quantity Currency  
1        1      CAD  
2        2      USD  
3        1      USD  
4        7      CAD  
5        1      CAD

# Custom Functions

In [8]:
def calcSales(data):
  return data['Quantity'] * data['UnitPriceUSD']

def calcProfit(data):
  return data['Quantity'] * (data['UnitPriceUSD'] - data['UnitCostUSD'])

# Pre-Processing

In [9]:
dfMain = pd.merge(dfSales, dfCustomers, how='inner', on='CustomerKey')
dfMain = pd.merge(dfMain, dfProducts, how='inner', on='ProductKey')
dfMain = dfMain.astype({'Quantity': 'int'})

dfMain["DeliveryDate"] = pd.to_datetime(dfMain["DeliveryDate"], format="%m/%d/%Y")
dfMain["OrderDate"] = pd.to_datetime(dfMain["OrderDate"], format="%m/%d/%Y")

dfMain["Birthday"] = dfMain["Birthday"].fillna(datetime.datetime.now().strftime('%m/%d/%Y'))
dfMain["Birthday"] = pd.to_datetime(dfMain["Birthday"], infer_datetime_format=True, errors='coerce')
current_year = datetime.datetime.now().year
dfMain['BirthYear'] = dfMain['Birthday'].dt.year
dfMain['Age'] = current_year - dfMain['BirthYear']

dfMain['BirthYear'] = dfMain['BirthYear'].fillna(0).astype('int64')
dfMain['Age'] = dfMain['Age'].fillna(0).astype('int64')
bins = [0, 5, 18, 30, 60, np.inf]
labels = ['Infant', 'YoungChild', 'Teenager', 'Adult', 'Elderly']
dfMain['Age'] = pd.cut(dfMain['Age'], bins=bins, labels=labels)

dfMain.drop_duplicates(keep="first", inplace=True)
dfMain["Sales"] = dfMain.apply(calcSales, axis=1)
dfMain["Profit"] = dfMain.apply(calcProfit, axis=1)

dfMain.drop(columns=['LineItem', 'CustomerKey', 'ProductKey', 'SubcategoryKey', 'CategoryKey', 'StateCode', 'ZipCode', 'DeliveryDate', 'Birthday', 'StoreKey', 'UnitCostUSD', 'UnitPriceUSD', 'BirthYear'], inplace=True)
dfMain = dfMain[dfMain['Profit'] <= 1000]
dfMain.shape

(54376, 18)

# Generic Info

In [17]:
dfMain.to_csv(datapath + '\\EMart.csv')
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
dfMain.head()

0 OrderNumber  OrderDate  Quantity Currency  Gender            Name  \
0      366000 2016-01-01         1      CAD    Male    Tyler Vaught   
1      366001 2016-01-01         2      USD    Male  Frank Upchurch   
2      366001 2016-01-01         1      USD    Male  Frank Upchurch   
4      366002 2016-01-01         1      CAD  Female      Joan Roche   
7      366004 2016-01-01         2      GBP    Male      Sam Nelson   

0              City            State         Country      Continent  \
0            London          Ontario          Canada  North America   
1           Auberry       California   United States  North America   
2           Auberry       California   United States  North America   
4          Red Deer          Alberta          Canada  North America   
7  BURSCOUGH BRIDGE  West Lancashire  United Kingdom         Europe   

0                                        ProductName              Brand  \
0                    Contoso Lens Adapter M450 White            Contoso   
1                    A. Datum SLR Camera X136 Silver           A. Datum   
2             Fabrikam Microwave 1.5CuFt X1100 Black           Fabrikam   
4              Adventure Works Laptop8.9 E0890 White    Adventure Works   
7  The Phone Company PDA Handheld 3.5 inch M610 B...  The Phone Company   

0   Color          Subcategory         Category       Age   Sales  Profit  \
0   White  CamCord Accessories   Cam & Recorder     Adult   68.00   36.73   
1  Silver  Digital SLR Cameras   Cam & Recorder  Teenager  854.00  571.06   
2   Black           Microwaves  Home Appliances  Teenager  665.94  445.30   
4   White              Laptops        Computers   Elderly  326.00  159.80   
7   Black  Smart phones & PDAs        CellPhone       NaN  510.00  275.46   

0 OrderMonth  
0 2016-01-01  
1 2016-01-01  
2 2016-01-01  
4 2016-01-01  
7 2016-01-01

In [12]:
print(dfMain.dtypes.value_counts())
dfMain.dtypes

object            13
datetime64[ns]     2
float64            2
int64              1
category           1
Name: count, dtype: int64


0
OrderNumber            object
OrderDate      datetime64[ns]
Quantity                int64
Currency               object
Gender                 object
Name                   object
City                   object
State                  object
Country                object
Continent              object
ProductName            object
Brand                  object
Color                  object
Subcategory            object
Category               object
Age                  category
Sales                 float64
Profit                float64
OrderMonth     datetime64[ns]
dtype: object

In [13]:
# Information about min, max, mean & percentile
dfMain.describe().T

count                           mean                  min  \
0                                                                         
OrderDate     54376  2018-12-05 12:09:57.440047360  2016-01-01 00:00:00   
Quantity    54376.0                       2.834633                  1.0   
Sales       54376.0                     439.996861                 0.95   
Profit      54376.0                     241.206474                 0.47   
OrderMonth    54376  2018-11-20 16:40:20.479623168  2016-01-01 00:00:00   

                            25%                  50%                  75%  \
0                                                                           
OrderDate   2018-02-03 00:00:00  2019-02-10 00:00:00  2019-11-25 00:00:00   
Quantity                    1.0                  2.0                  4.0   
Sales                     89.95               279.99                657.0   
Profit                    47.03               150.16               366.22   
OrderMonth  2018-02-01 00:00:00  2019-02-01 00:00:00  2019-11-01 00:00:00   

                            max         std  
0                                            
OrderDate   2021-02-20 00:00:00         NaN  
Quantity                   10.0    2.036626  
Sales                    2032.0  444.845878  
Profit                    999.7  244.983572  
OrderMonth  2021-02-01 00:00:00         NaN

In [14]:
# Information about count, top & uniqueness
dfMain.describe(include='object').T.sort_values(by='unique')

count unique                             top   freq
0                                                               
Gender       54376      2                            Male  27444
Continent    53708      3                   North America  33899
Currency     54376      5                             USD  29229
Country      54277      8                   United States  29229
Category     54376      9                       Computers   9586
Brand        54376     11                         Contoso  14370
Color        54376     16                           Black  14386
Subcategory  54376     32                       Movie DVD   8843
State        54376    489                      California   3143
ProductName  54376   2313  WWI Desktop PC1.60 E1600 Black    155
City         54376   6466                         Toronto    591
Name         54376  11565                Gaspare Trevisan     30
OrderNumber  54376  24993                         1629012      7

* Checking & Treating Null Values

In [15]:
# We have 0% of the null values are present
# round(dfMain.isna().sum()/dfMain.shape[0]*100, 4)
missing_value = pd.DataFrame({
    'TotalMissing' : dfMain.isnull().sum(),
    'Percentage' : (dfMain.isnull().sum()/len(dfMain))*100 })
missing_value[missing_value['Percentage'] > 0].sort_values(by='Percentage',ascending=False)

TotalMissing  Percentage
0                                  
Age                8359   15.372591
Continent           668    1.228483
Country              99    0.182066

In [ ]:
num_features = list(dfMain.select_dtypes(include=["float", "int"]).columns)
cat_features = list(dfMain.select_dtypes(include=["object"]).columns)

print(f"We have {len(num_features)} Numerical Features: {num_features}")
print(f"We have {len(cat_features)} Categorical Features: {cat_features}")
for col in dfMain.columns:
  if (dfMain[col].nunique() < 30):
    print(f"\nWe have {dfMain[col].nunique()} categories of {col}:\n", dfMain[col].unique())

# Uni-Variate Analysis

In [11]:

# 1. Sales by Category
sales_by_category = dfMain.groupby('Category')['Quantity'].sum().reset_index()
trace1 = go.Bar(x=sales_by_category['Category'], y=sales_by_category['Quantity'], name='Sales by Category')

# 2. Sales Trend Over Time
dfMain['OrderMonth'] = dfMain['OrderDate'].dt.to_period('M').dt.to_timestamp()
sales_trend = dfMain.groupby('OrderMonth')['Quantity'].sum().reset_index()
trace2 = go.Scatter(
    x=sales_trend['OrderMonth'],
    y=sales_trend['Quantity'],
    mode='lines+markers',
    name='Sales Trend Over Time'
)

# 3. Customer Demographics - Age Distribution
trace3 = go.Histogram(x=dfMain['Age'], name='Customer Age Distribution')

# 4. Customer Demographics - Gender Distribution
trace4 = go.Pie(labels=dfMain['Gender'].value_counts().index,
    values=dfMain['Gender'].value_counts().values, name='Customer Gender Distribution')

# 5. Sales Distribution
trace5 = go.Histogram(x=dfMain['Sales'], name='Sales Distribution')

# 6. Profit Distribution
trace6 = go.Histogram(x=dfMain['Profit'], name='Profit Distribution')

# 7. Quantity Distribution
trace7 = go.Histogram(x=dfMain['Quantity'], name='Quantity Distribution')

# 8. Currency Distribution
trace8 = go.Histogram(x=dfMain['Currency'], hoverinfo='x+text', name='Currency Distribution')

# 9. Country Distribution
trace9 = go.Histogram(x=dfMain['Country'], hoverinfo='x+text', name='Country Distribution')

# 10. Continent Distribution
trace10 = go.Histogram(x=dfMain['Continent'], hoverinfo='x+text', name='Continent Distribution')

# 11. Subcategory Distribution
trace11 = go.Histogram(x=dfMain['Subcategory'], hoverinfo='x+text', name='Subcategory Distribution')

# 11. Subcategory Distribution
# Calculate the correlation matrix
corr_matrix = dfMain[['Quantity', 'Sales', 'Profit']].corr()

# Create the heatmap trace
trace12 = go.Heatmap(z=corr_matrix.values, x=corr_matrix.columns, y=corr_matrix.columns,
                      colorscale='Viridis', showscale=False, zmin=-1, zmax=1)

# Create subplots
fig = make_subplots(rows=4, cols=3, specs=[[{}, {}, {}], [{"type": "pie"}, {}, {}], [{}, {}, {}], [{}, {}, {}]],
    subplot_titles=(
        'Sales by Category', 'Sales Trend Over Time', 'Customer Age Distribution', 'Customer Gender Distribution', 'Sales Distribution', 'Profit Distribution',
        'Quantity Distribution', 'Currency Distribution', 'Country Distribution', 'Continent Distribution', 'SubCategory Distribution', 'Correlation Matrix' ) )

# Add traces to subplots
fig.add_trace(trace1, row=1, col=1)
fig.add_trace(trace2, row=1, col=2)
fig.add_trace(trace3, row=1, col=3)
fig.add_trace(trace4, row=2, col=1)
fig.add_trace(trace5, row=2, col=2)
fig.add_trace(trace6, row=2, col=3)
fig.add_trace(trace7, row=3, col=1)
fig.add_trace(trace8, row=3, col=2)
fig.add_trace(trace9, row=3, col=3)
fig.add_trace(trace10, row=4, col=1)
fig.add_trace(trace11, row=4, col=2)
fig.add_trace(trace12, row=4, col=3)

# Update layout for the overall figure
fig.update_layout(height=1200, width=1800, title_text="Dashboard", showlegend=True)

# Show the figure
fig.show()

# Bi-Variate Analysis

# Multi-Variate Analysis

# Hypothesis Testing

# Insights & Recommendations